## QQQ EDA

### Import Libraries

In [188]:
from datetime import datetime, timedelta
import yfinance as yf
import talib

import pandas as pd
import numpy as np
import plotly.graph_objs as go



### Import QQQ historical data

In [152]:
ticker = yf.Ticker("QQQ")
df = ticker.history(period="max")
df

Open        High         Low       Close    Volume  \
Date                                                                   
1999-03-10   43.960006   43.986877   43.234505   43.906265   5232000   
1999-03-11   44.228701   44.483970   43.261366   44.121220   9688600   
1999-03-12   43.960004   43.986874   42.697094   43.046410   8743600   
1999-03-15   43.368846   44.336181   42.912049   44.282440   6369000   
1999-03-16   44.470545   44.846731   43.986878   44.658638   4905800   
...                ...         ...         ...         ...       ...   
2023-03-09  298.329987  300.980011  291.829987  292.660004  71456700   
2023-03-10  292.829987  294.350006  287.380005  288.549988  98479500   
2023-03-13  286.730011  294.470001  285.190002  290.690002  97123600   
2023-03-14  294.309998  297.929993  293.450012  297.369995  73421500   
2023-03-15  294.709991  296.170013  293.250000  295.640015  29031123   

            Dividends  Stock Splits  
Date                                 
1999-03-10        0.0           0.0  
1999-03-11        0.0           0.0  
1999-03-12        0.0           0.0  
1999-03-15        0.0           0.0  
1999-03-16        0.0           0.0  
...               ...           ...  
2023-03-09        0.0           0.0  
2023-03-10        0.0           0.0  
2023-03-13        0.0           0.0  
2023-03-14        0.0           0.0  
2023-03-15        0.0           0.0  

[6044 rows x 7 columns]

### QQQ Description

#### statistics

In [153]:
df.describe()

Open         High          Low        Close        Volume  \
count  6044.000000  6044.000000  6044.000000  6044.000000  6.044000e+03   
mean     99.154520    99.986596    98.227663    99.155247  6.724365e+07   
std      91.789607    92.523086    90.980617    91.809812  5.011119e+07   
min      17.145476    17.652789    16.990698    17.248657  3.302000e+06   
25%      36.221314    36.588091    35.931717    36.210904  3.043988e+07   
50%      57.393939    57.863252    56.887452    57.344166  5.535055e+07   
75%     125.439671   125.864598   124.937581   125.398449  8.994840e+07   
max     402.089441   405.202478   399.125046   400.528290  6.167723e+08   

         Dividends  Stock Splits  
count  6044.000000   6044.000000  
mean      0.002830      0.000331  
std       0.031226      0.025726  
min       0.000000      0.000000  
25%       0.000000      0.000000  
50%       0.000000      0.000000  
75%       0.000000      0.000000  
max       0.655000      2.000000

#### Any NaN values?

In [154]:
# Check for missing values in the entire DataFrame
na_values = df.isna().any()
print(na_values)

Open            False
High            False
Low             False
Close           False
Volume          False
Dividends       False
Stock Splits    False
dtype: bool


#### how many times QQQ performed stock split?

In [155]:
stock_splits_count = (df['Stock Splits'] != 0).sum()
stock_splits_time = df.index[df['Stock Splits'] != 0]
print("QQQ performed {} stock splits: at {}".format(stock_splits_count, stock_splits_time[0]))

QQQ performed 1 stock splits: at 2000-03-20 00:00:00


#### Stock trend plot

In [156]:
# Plot the stock price trend
fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=df['Close'], name='Stock Price'))

fig.update_layout(
    title='Stock Price Trend',
    xaxis_title='Date',
    yaxis_title='Price'
)

fig.show()

### Correlations of indicators (vs. price) 

#### Simple Moving Average (SMA)

In [229]:

df['SMA'] = talib.SMA(df['Close'], timeperiod=14)

sma_fig = go.Figure()
sma_fig.add_trace(go.Scatter(x=df.index, y=df['Close'], name='Stock Price'))
sma_fig.add_trace(go.Scatter(x=df.index, y=df['SMA'] , name='SMA'))


sma_fig.update_layout(
    title='SMA vs. Price',
    xaxis_title='Date',
    yaxis_title='Price'
)

sma_fig.show()

#### EMA (Exponential Moving Average)

In [228]:

df['EMA'] = talib.EMA(df['Close'], timeperiod=60)

sma_fig = go.Figure()
sma_fig.add_trace(go.Scatter(x=df.index, y=df['Close'], name='Stock Price'))
sma_fig.add_trace(go.Scatter(x=df.index, y=df['EMA'] , name='EMA'))


sma_fig.update_layout(
    title='EMA vs. Price',
    xaxis_title='Date',
    yaxis_title='Price'
)

sma_fig.show()

#### DOJI (open and close levels that are virtually equal)

In [230]:

df["DOJI"] = talib.CDLDOJI(df['Open'], df['High'], df['Low'], df['Close'])

# Create a new column for the y-coordinates of the red dots
df["DOJI_Y"] = df.apply(lambda row: row["Close"] if row["DOJI"] == 100 else None, axis=1)

dema_fig = go.Figure()
dema_fig.add_trace(go.Scatter(x=df.index, y=df["Close"], name='Price'))
dema_fig.add_trace(go.Scatter(x=df.index, y=df["DOJI_Y"], mode='markers', marker=dict(color='red'), name='DOJI'))

dema_fig.update_layout(
    title='DOJI vs. Price',
    xaxis_title='Date',
    yaxis_title='Price'
)

dema_fig.show()

#### Momentum (MOM)

In [231]:
df["MOM"] = talib.MOM(df['Close'], timeperiod=5)

mom_fig = go.Figure()
mom_fig.add_trace(go.Scatter(x=df.index, y=df["Close"] , name='Price'))
mom_fig.add_trace(go.Scatter(x=df.index, y=df['MOM'] , name='MOM'))

mom_fig.update_layout(
    title='MOM vs. Price',
    xaxis_title='Date',
    yaxis_title='Price'
)

mom_fig.show()

### SMA Strategy BackTest

In [316]:
'''
Long Entry: when close price exceed SMA
Short Entry: when close price below SMA
'''

# capital init
capital = 10000
prev_trade = { 'position': None, 'price': 0, 'shares': 0, 'amount':0 }
value = capital + prev_trade['amount']


# time period (format: 'YYYY-MM-DD')
start_date = '2010-02-19'
end_date = '2020-03-18'
start_idx = df.index.get_loc(start_date)
end_idx = df.index.get_loc(end_date)

# calculate ROI
ROI = pd.DataFrame.from_dict({
    'Date':[],
    'Value':[],
    'Long_entry': [],
    'Short_entry': []
})
prev_price = df.iloc[start_idx]['Close']
for idx, row in df.iloc[start_idx:end_idx].iterrows():
    long_entry = False
    short_entry = False
    # long entry
    if (row['Close'] > row['SMA']):
        # if current in short position
        if prev_trade['position'] == 'short':
            # short exist
            gain_loss_per_share = prev_price - row['Close']
            gain_loss_total = gain_loss_per_share * prev_trade['shares']
            retrive_capital = prev_trade['amount'] + gain_loss_total
            capital += retrive_capital
        elif prev_trade['position'] == 'long':
            # calculate current account value: capital + position amount
            gain_loss_per_share = row['Close'] - prev_price 
            gain_loss_total = gain_loss_per_share * prev_trade['shares']
            prev_trade['amount'] += gain_loss_total
            value = capital + prev_trade['amount']
            ROI = ROI.append({'Date': idx, 'Value': value, 'Long_entry': False, 'Short_entry': False}, ignore_index=True)
            prev_price = row['Close'] # record current price
            continue
        # enter long position (regarless short or none position)
        position = 'long'
        price = row['Close']
        shares = capital // price
        amount = shares * price
        capital -= amount
        prev_trade['position'] = position
        prev_trade['price'] = price
        prev_trade['shares'] = shares
        prev_trade['amount'] = amount
        value = capital + prev_trade['amount']
        long_entry = True

    # short entry
    elif (row['Close'] < row['SMA']):
        # if current in long position:
        if prev_trade['position'] == 'long':
            # long exit
            gain_loss_per_share = row['Close'] - prev_price
            gain_loss_total = gain_loss_per_share * prev_trade['shares']
            retrive_capital = prev_trade['amount'] + gain_loss_total
            capital += retrive_capital
        elif prev_trade['position'] == 'short':
            # calculate current account value: capital + position amount
            gain_loss_per_share = prev_price - row['Close']
            gain_loss_total = gain_loss_per_share * prev_trade['shares']
            prev_trade['amount'] += gain_loss_total
            value = capital + prev_trade['amount']
            ROI = ROI.append({'Date':idx, 'Value': value, 'Long_entry': False, 'Short_entry': False}, ignore_index=True)
            prev_price = row['Close'] # record current price
            continue
        # enter short position (regarless short or none position)
        position = 'short'
        price = row['Close']
        shares = capital // price
        amount = shares * price
        capital -= amount
        prev_trade['position'] = position
        prev_trade['price'] = price
        prev_trade['shares'] = shares
        prev_trade['amount'] = amount
        value = capital + prev_trade['amount']
        short_entry = True

    # record current price
    prev_price = row['Close']

    # append current capital level
    ROI = ROI.append({'Date':idx, 'Value': value, 'Long_entry': long_entry, 'Short_entry': short_entry}, ignore_index=True)


# convert QQQ and ROI['Value'] to percentage change
ROI['QQQ'] = df[start_idx:end_idx]['Close'].values
ROI['ValuePctChange'] = (ROI['Value'] / ROI.iloc[0]['Value']) * 100
ROI['QQQPctChange'] = (ROI['QQQ'] / ROI.iloc[0]['QQQ']) * 100

# y-coordinates of the long_entry and short_entry
ROI["Long_entry"] = ROI.apply(lambda row: row["ValuePctChange"] if row["Long_entry"] else None, axis=1)
ROI["Short_entry"] = ROI.apply(lambda row: row["ValuePctChange"] if row["Short_entry"] else None, axis=1)

# ROI plot
sma_roi_fig = go.Figure()
sma_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["ValuePctChange"], name='SMA Strategy ROI'))
sma_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["QQQPctChange"], name='QQQ PctChange'))
sma_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["Long_entry"], mode='markers', marker=dict(color='green'), name='Long Entry'))
sma_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["Short_entry"], mode='markers', marker=dict(color='red'), name='Short Entry'))

sma_roi_fig.update_layout(
    title='SMA Strategy ROI vs. QQQ ROI',
    xaxis_title='Date',
    yaxis_title='Pct Change'
)

sma_roi_fig.show()


### DOJI & EMA Strategy Backtest

In [298]:
'''
Entry: Long entry only, when DOJI occurs above the EMA60
Exist: hit profit target or stop loss limit
'''

# capital init
capital = 10000
stop_loss_pct = -0.2
stop_profit_pct = 0.1
stop_loss = stop_loss_pct * 10000
stop_profit = stop_profit_pct * 10000
prev_trade = { 'position': False, 'price': 0, 'shares': 0, 'amount':0, 'gain_loss':0 }
value = capital + prev_trade['amount']


# time period (format: 'YYYY-MM-DD')
start_date = '2015-02-19'
end_date = '2019-03-14'
start_idx = df.index.get_loc(start_date)
end_idx = df.index.get_loc(end_date)

# calculate ROI
ROI = pd.DataFrame.from_dict({
    'Date':[],
    'Value':[],
    'Entry':[],
    'Exit':[],
})
prev_price = df.iloc[start_idx]['Close']
for idx, row in df.iloc[start_idx:end_idx].iterrows():
    stop_loss = prev_trade['amount'] * stop_loss_pct
    stop_profit = prev_trade['amount'] * stop_profit_pct
    Entry = False
    Exit = False
    # long entry
    if ((prev_trade['position'] == False) &
        (row['DOJI'] != 0) & 
        (row['Close'] > row['EMA']) 
        ):
        # enter long position
        price = row['Close']
        shares = capital // price
        amount = shares * price
        capital -= amount
        prev_trade = { 'position': True, 'price': price, 'shares': shares, 'amount':amount, 'gain_loss':0 }
        Entry = True
    # long exit
    elif ((prev_trade['position'] == True) &
          ((prev_trade['gain_loss'] <= stop_loss) |
           (prev_trade['gain_loss'] >= stop_profit))
         ):
        gain_loss_per_share = row['Close'] - prev_price
        gain_loss_total = gain_loss_per_share * prev_trade['shares']
        retrive_capital = prev_trade['amount'] + gain_loss_total
        capital += retrive_capital
        prev_trade = { 'position': False, 'price': 0, 'shares': 0, 'amount':0, 'gain_loss':0 }
        Exit = True
    # if position exist
    else:
        # calculate current account value: capital + position amount
        gain_loss_per_share = row['Close'] - prev_price 
        gain_loss_total = gain_loss_per_share * prev_trade['shares']
        prev_trade['amount'] += gain_loss_total
        prev_trade['gain_loss'] += gain_loss_total

    # record current price
    prev_price = row['Close']

    # append current account value level
    value = capital + prev_trade['amount']
    ROI = ROI.append({'Date':idx, 'Value': value,'Entry': Entry, 'Exit': Exit}, ignore_index=True)


# convert QQQ and ROI['Value'] to percentage change
ROI['QQQ'] = df[start_idx:end_idx]['Close'].values
ROI['ValuePctChange'] = (ROI['Value'] / ROI.iloc[0]['Value']) * 100
ROI['QQQPctChange'] = (ROI['QQQ'] / ROI.iloc[0]['QQQ']) * 100

# y-coordinates of the Entry and Exit
ROI["Entry_Y"] = ROI.apply(lambda row: row["ValuePctChange"] if row["Entry"] else None, axis=1)
ROI["Exit_Y"] = ROI.apply(lambda row: row["ValuePctChange"] if row["Exit"] else None, axis=1)

# ROI plot
doji_roi_fig = go.Figure()
doji_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["ValuePctChange"], name='DOJI Strategy ROI'))
doji_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["QQQPctChange"], name='QQQ PctChange'))
doji_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["Entry_Y"], mode='markers', marker=dict(color='green'), name='Entry'))
doji_roi_fig.add_trace(go.Scatter(x=ROI['Date'], y=ROI["Exit_Y"], mode='markers', marker=dict(color='red'), name='Exit'))



doji_roi_fig.update_layout(
    title='DOJI Strategy ROI vs. QQQ ROI',
    xaxis_title='Date',
    yaxis_title='Pct Change'
)

doji_roi_fig.show()
